In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
import qt
import requests

from qt import dt, np, pd

In [3]:
from eodhd import *

- save nasdaq 100 constituents

In [4]:
t_nasdaq = get_index_composition("NDX.INDX")
t_nasdaq.to_csv('data/nasdaq100_20260204.csv', index=False)
# get_ndx_historical_changes()

- read a specific flat file

In [ ]:
date = dt.date(2026, 1, 12)

In [9]:
flat_file_name = date.strftime("data/flat_csv/%Y-%m-%d.csv")
flat_file_name

'data/flat_csv/2026-01-12.csv'

In [11]:
t = pd.read_csv(flat_file_name)

In [14]:
tn = t[t['ticker'].str.contains("NVDA")].reset_index(drop=True)

In [26]:
import pytz
def process_options_data(df):
	"""
	1. Converts Unix nanosecond timestamps to US/Eastern time.
	2. Extracts Root, Expiry, Type, and Strike from the OSI ticker string.
	"""
	
	# 1. Convert Unix Nanoseconds to US/Eastern Time
	# Massive/Polygon timestamps are in nanoseconds (19 digits)
	df['timestamp_utc'] = pd.to_datetime(df['window_start'], unit='ns', utc=True)
	
	# Convert to US/Eastern (market time)
	eastern = pytz.timezone('US/Eastern')
	df['timestamp_ny'] = df['timestamp_utc'].dt.tz_convert(eastern)

	# 2. Parse the OSI Ticker String (O:ROOTYYMMDDTCSSSSSSSS)
	# Strip the 'O:' prefix first
	clean_ticker = df['ticker'].str.replace('O:', '', regex=False)
	
	# Extract components by position
	# Root: Characters from start until the first digit (Expiry)
	df['root'] = clean_ticker.str.extract(r'^([A-Z]+)')
	
	# Expiry: 6 digits following the root (YYMMDD)
	expiry_str = clean_ticker.str.extract(r'(\d{6})')[0]
	df['expiry'] = pd.to_datetime(expiry_str, format='%y%m%d').dt.date
	
	# Type: The single character (C/P) after the 6-digit date
	df['type'] = clean_ticker.str.extract(r'\d{6}([CP])')[0].map({'C': 'Call', 'P': 'Put'})
	
	# Strike: The last 8 digits, divided by 1000
	strike_int = clean_ticker.str.extract(r'([CP])(\d{8})')[1].astype(float)
	df['strike_usd'] = strike_int / 1000.0
	
	return df

In [27]:
process_options_data(tn)

ticker  volume   open  close   high    low  \
0      O:NVDA260116C00000500       1 185.17 185.17 185.17 185.17   
1      O:NVDA260116C00000500       2 184.70 184.70 184.70 184.70   
2      O:NVDA260116C00000500       2 184.62 184.62 184.62 184.62   
3      O:NVDA260116C00000500       1 184.70 184.70 184.70 184.70   
4      O:NVDA260116C00000500       1 184.17 184.17 184.17 184.17   
...                      ...     ...    ...    ...    ...    ...   
58194  O:NVDA281215P00300000      20 125.51 125.51 125.51 125.51   
58195  O:NVDA281215P00320000       2 142.33 142.40 142.40 142.33   
58196  O:NVDA281215P00340000       2 159.62 159.68 159.68 159.62   
58197  O:NVDA281215P00370000       2 186.10 185.90 186.10 185.90   
58198  O:NVDA281215P00380000       2 196.34 196.38 196.38 196.34   

              window_start  transactions             timestamp_utc  \
0      1768228620000000000             1 2026-01-12 14:37:00+00:00   
1      1768228920000000000             1 2026-01-12 14:42:00+00:00   
2      1768228980000000000             1 2026-01-12 14:43:00+00:00   
3      1768229040000000000             1 2026-01-12 14:44:00+00:00   
4      1768233660000000000             1 2026-01-12 16:01:00+00:00   
...                    ...           ...                       ...   
58194  1768249500000000000             1 2026-01-12 20:25:00+00:00   
58195  1768240620000000000             2 2026-01-12 17:57:00+00:00   
58196  1768240680000000000             2 2026-01-12 17:58:00+00:00   
58197  1768245300000000000             2 2026-01-12 19:15:00+00:00   
58198  1768237140000000000             2 2026-01-12 16:59:00+00:00   

                   timestamp_ny  root      expiry  type  strike_usd  
0     2026-01-12 09:37:00-05:00  NVDA  2026-01-16  Call        0.50  
1     2026-01-12 09:42:00-05:00  NVDA  2026-01-16  Call        0.50  
2     2026-01-12 09:43:00-05:00  NVDA  2026-01-16  Call        0.50  
3     2026-01-12 09:44:00-05:00  NVDA  2026-01-16  Call        0.50  
4     2026-01-12 11:01:00-05:00  NVDA  2026-01-16  Call        0.50  
...                         ...   ...         ...   ...         ...  
58194 2026-01-12 15:25:00-05:00  NVDA  2028-12-15   Put      300.00  
58195 2026-01-12 12:57:00-05:00  NVDA  2028-12-15   Put      320.00  
58196 2026-01-12 12:58:00-05:00  NVDA  2028-12-15   Put      340.00  
58197 2026-01-12 14:15:00-05:00  NVDA  2028-12-15   Put      370.00  
58198 2026-01-12 11:59:00-05:00  NVDA  2028-12-15   Put      380.00  

[58199 rows x 14 columns]

In [29]:
def download_nvda_intraday(symbol, api_token=EODHD_API_KEY):
	interval = "1m"
	base_url = f"https://eodhd.com/api/intraday/{symbol}"
	
	# Calculate date ranges: 6 months total, split into two 90-day chunks
	end_date = dt.datetime.now()
	mid_date = end_date - dt.timedelta(days=90)
	start_date = end_date - dt.timedelta(days=180)
	
	chunks = [
		(start_date, mid_date),
		(mid_date + dt.timedelta(seconds=1), end_date)
	]
	
	all_data = []
	
	for start, end in chunks:
		params = {
			"api_token": api_token,
			"interval": interval,
			"fmt": "json",
			"from": int(start.timestamp()),
			"to": int(end.timestamp())
		}
		
		response = requests.get(base_url, params=params)
		
		if response.status_code == 200:
			all_data.extend(response.json())
		else:
			print(f"Error fetching chunk {start.date()} to {end.date()}: {response.status_code}")

	# Convert to DataFrame
	df = pd.DataFrame(all_data)
	
	# Format and set index
	if not df.empty:
		# EODHD returns 't' as a Unix timestamp (seconds)
		df['datetime'] = pd.to_datetime(df['timestamp'], unit='s', utc=True)
		df.set_index('datetime', inplace=True)
		# Rename columns to standard OHLCV
		df.rename(columns={'o': 'open', 'h': 'high', 'l': 'low', 'c': 'close', 'v': 'volume'}, inplace=True)
		
	return df

In [30]:
nvda_6m_df = download_nvda_intraday("NVDA.US")

In [32]:
nvda_6m_df['close'].plot()